# Building a base map in Altair

#### Editing in MapShaper

My primary source is the [UC Berkeley Geodata Repository](https://geodata.lib.berkeley.edu).  I'm starting with an [overview of the Bay Area](https://geodata.lib.berkeley.edu/catalog/ark28722-s7d02x) publsihed by the City of San Francisco.  I imported this map into [mapshaper](https://mapshaper.org) and clipped it to an area that covered the Bay completely from north to south.  This may not be an optimal scale, and Vega-Lite unfortunately does not support panning and zooming.

#### Load libraries

In [4]:
import altair as alt
import pandas as pd
import geopandas as gpd
from shapely.geometry import Polygon, Point, LineString

#### Load and render the first map

In [18]:
base_1 = gpd.read_file('../project_flask/static/data/small_bay_topo.json')
base_1.head()

id  OBJECTID                                           geometry
0  s7vw2x.1         1  MULTIPOLYGON (((-122.59370 37.86797, -122.5934...

In [19]:
def base_map(df, color='#333333', dimensions=(880, 800), projection='mercator'):
    rendered_map = alt.Chart(df).mark_geoshape(color=color, strokeWidth=0).encode().project(
        type=projection, 
    ).properties(
        width=dimensions[0],
        height=dimensions[1]
    )
    return rendered_map

In [20]:
base = base_map(base_1)
base

alt.Chart(...)

#### Adding geographic labels

In [21]:
locations = [['San Francisco', 37.78, -122.44],
             ['Oakland', 37.811816, -122.275828],
             ['Richmond', 37.936, -122.348282],
             ['Benicia', 38.07, -122.145650]
            ]

locations_df = pd.DataFrame(locations, columns=['Name', 'LAT', 'LON'])
locations_df

Name        LAT         LON
0  San Francisco  37.780000 -122.440000
1        Oakland  37.811816 -122.275828
2       Richmond  37.936000 -122.348282
3        Benicia  38.070000 -122.145650

In [22]:
text_annotations = alt.Chart(locations_df).mark_text(angle=0, font='Roboto-Thin.ttf').encode(text='Name:N', latitude='LAT', longitude='LON')

In [23]:
base + text_annotations

alt.LayerChart(...)

#### Adding the bridges

In [85]:
bridges = [['Golden Gate', 37.825544, -122.479248],
           ['Golden Gate', 37.810238, -122.477471],
           ['Bay Bridge West', 37.789310, -122.387434],
           ['Bay Bridge West', 37.807916, -122.367529],
           ['Bay Bridge East', 37.814503, -122.359903],
           ['Bay Bridge East', 37.817503, -122.354686],
           ['Bay Bridge East', 37.818503, -122.352336],
           ['Bay Bridge East', 37.818986, -122.350373],
           ['Bay Bridge East', 37.821672, -122.331211],
           ['Bay Bridge East', 37.822019, -122.327145],
           ['Richmond-San Rafael', 37.942801, -122.479133],
           ['Richmond-San Rafael', 37.941143, -122.470174],
           ['Richmond-San Rafael', 37.939908, -122.465561],
           ['Richmond-San Rafael', 37.936752, -122.455369],
           ['Richmond-San Rafael', 37.936168, -122.453309],
           ['Richmond-San Rafael', 37.935660, -122.450702],
           ['Richmond-San Rafael', 37.935406, -122.448417],
           ['Richmond-San Rafael', 37.932674, -122.408188],
           ['Richmond-San Rafael', 37.932369, -122.404873]
          ]

In [86]:
bridges = gpd.GeoDataFrame(bridges, columns=['Name', 'LAT', 'LON'])
bridge_points = [Point(xy) for xy in zip(bridges.LON, bridges.LAT)]
bridges['geometry'] = bridge_points

In [87]:
bridges

Name        LAT         LON                     geometry
0           Golden Gate  37.825544 -122.479248  POINT (-122.47925 37.82554)
1           Golden Gate  37.810238 -122.477471  POINT (-122.47747 37.81024)
2       Bay Bridge West  37.789310 -122.387434  POINT (-122.38743 37.78931)
3       Bay Bridge West  37.807916 -122.367529  POINT (-122.36753 37.80792)
4       Bay Bridge East  37.814503 -122.359903  POINT (-122.35990 37.81450)
5       Bay Bridge East  37.817503 -122.354686  POINT (-122.35469 37.81750)
6       Bay Bridge East  37.818503 -122.352336  POINT (-122.35234 37.81850)
7       Bay Bridge East  37.818986 -122.350373  POINT (-122.35037 37.81899)
8       Bay Bridge East  37.821672 -122.331211  POINT (-122.33121 37.82167)
9       Bay Bridge East  37.822019 -122.327145  POINT (-122.32715 37.82202)
10  Richmond-San Rafael  37.942801 -122.479133  POINT (-122.47913 37.94280)
11  Richmond-San Rafael  37.941143 -122.470174  POINT (-122.47017 37.94114)
12  Richmond-San Rafael  37.939908 -122.465561  POINT (-122.46556 37.93991)
13  Richmond-San Rafael  37.936752 -122.455369  POINT (-122.45537 37.93675)
14  Richmond-San Rafael  37.936168 -122.453309  POINT (-122.45331 37.93617)
15  Richmond-San Rafael  37.935660 -122.450702  POINT (-122.45070 37.93566)
16  Richmond-San Rafael  37.935406 -122.448417  POINT (-122.44842 37.93541)
17  Richmond-San Rafael  37.932674 -122.408188  POINT (-122.40819 37.93267)
18  Richmond-San Rafael  37.932369 -122.404873  POINT (-122.40487 37.93237)

In [88]:
bridges = bridges.groupby(['Name'])['geometry'].apply(lambda x: LineString(x.tolist()))
bridges = gpd.GeoDataFrame(bridges)

In [89]:
bridges

geometry
Name                                                                  
Bay Bridge East      LINESTRING (-122.35990 37.81450, -122.35469 37...
Bay Bridge West      LINESTRING (-122.38743 37.78931, -122.36753 37...
Golden Gate          LINESTRING (-122.47925 37.82554, -122.47747 37...
Richmond-San Rafael  LINESTRING (-122.47913 37.94280, -122.47017 37...

In [94]:
bridge_map = alt.Chart(bridges).mark_geoshape(filled=False,
                                              color='white',
                                              strokeWidth=1.25)

In [95]:
base + bridge_map

alt.LayerChart(...)